In [1]:
using Revise

In [2]:
using MeshCat
using MeshCatMechanisms
using RigidBodyDynamics
using JuMP
using Gurobi
using JLD2
using Flux
using MLDataPattern
using ProgressMeter
using Plots; gr()

Plots.GRBackend()

In [3]:
import LCPSim
import BoxValkyries
import FluxExtensions

INFO: Recompiling stale cache file /home/rdeits/locomotion/explorations/learning-mpc/packages/lib/v0.6/LearningMPC.ji for module LearningMPC.
INFO: Recompiling stale cache file /home/rdeits/locomotion/explorations/learning-mpc/packages/lib/v0.6/BoxValkyries.ji for module BoxValkyries.


In [4]:
robot = BoxValkyries.BoxValkyrie()
mvis = MechanismVisualizer(robot)
IJuliaCell(mvis)

Listening on 127.0.0.1:7000...
zmq_url=tcp://127.0.0.1:6000
web_url=http://127.0.0.1:7000/static/


MeshCat.IJuliaCell(MeshCat.ViewerWindow(ZMQ.Context(Ptr{Void} @0x00000000060b3ef0, ZMQ.Socket[ZMQ.Socket(Ptr{Void} @0x00000000060e8b50, Base.Filesystem._FDWatcher(Ptr{Void} @0x00000000060be930, 55, (1, 0), Condition(Any[]), (false, false), 0))]), ZMQ.Socket(Ptr{Void} @0x00000000060e8b50, Base.Filesystem._FDWatcher(Ptr{Void} @0x00000000060be930, 55, (1, 0), Condition(Any[]), (false, false), 0)), "http://127.0.0.1:7000/static/", "tcp://127.0.0.1:6000", MeshCat.ZMQServer.ZMQWebSocketBridge(ip"127.0.0.1", Set{WebSockets.WebSocket}(), MeshCat.SceneTrees.SceneNode(Nullable{Array{UInt8,1}}(), Nullable{Array{UInt8,1}}(), Dict("meshcat"=>MeshCat.SceneTrees.SceneNode(#NULL, #NULL, Dict("robot"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x68, 0x63, 0x61, 0x74, 0x2f, 0x72, 0x6f, 0x62, 0x6f, 0x74], Dict("world"=>MeshCat.SceneTrees.SceneNode(#NULL, #NULL, Dict("dummy"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x6f, 0x72, 0x6c, 0x64, 0x2f, 0x64, 0x75, 0x6d, 0x6d, 0x79], Dict("base"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x64, 0x75, 0x6d, 0x6d, 0x79, 0x2f, 0x62, 0x61, 0x73, 0x65], Dict("base_revolute"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x65, 0x5f, 0x72, 0x65, 0x76, 0x6f, 0x6c, 0x75, 0x74, 0x65], Dict("core"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x6f, 0x6c, 0x75, 0x74, 0x65, 0x2f, 0x63, 0x6f, 0x72, 0x65], Dict("rh_dummy"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x65, 0x2f, 0x72, 0x68, 0x5f, 0x64, 0x75, 0x6d, 0x6d, 0x79], Dict("after_core_to_rh_rotation"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x68, 0x5f, 0x72, 0x6f, 0x74, 0x61, 0x74, 0x69, 0x6f, 0x6e], Dict("geometry_2"=>MeshCat.SceneTrees.SceneNode(UInt8[0x83, 0xa6, 0x6f, 0x62, 0x6a, 0x65, 0x63, 0x74, 0x84, 0xaa  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x32], UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x32], Dict{String,MeshCat.SceneTrees.SceneNode}()))),"rh"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x68, 0x5f, 0x64, 0x75, 0x6d, 0x6d, 0x79, 0x2f, 0x72, 0x68], Dict("after_core_to_rh_extension"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x5f, 0x65, 0x78, 0x74, 0x65, 0x6e, 0x73, 0x69, 0x6f, 0x6e], Dict("geometry_3"=>MeshCat.SceneTrees.SceneNode(UInt8[0x83, 0xa6, 0x6f, 0x62, 0x6a, 0x65, 0x63, 0x74, 0x84, 0xaa  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x33], UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x33], Dict{String,MeshCat.SceneTrees.SceneNode}()))))))),"rf_dummy"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x65, 0x2f, 0x72, 0x66, 0x5f, 0x64, 0x75, 0x6d, 0x6d, 0x79], Dict("after_core_to_rf_rotation"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x66, 0x5f, 0x72, 0x6f, 0x74, 0x61, 0x74, 0x69, 0x6f, 0x6e], Dict("geometry_6"=>MeshCat.SceneTrees.SceneNode(UInt8[0x83, 0xa6, 0x6f, 0x62, 0x6a, 0x65, 0x63, 0x74, 0x84, 0xaa  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x36], UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x67, 0x65, 0x6f, 0x6d, 0x65, 0x74, 0x72, 0x79, 0x5f, 0x36], Dict{String,MeshCat.SceneTrees.SceneNode}()))),"rf"=>MeshCat.SceneTrees.SceneNode(#NULL, UInt8[0x83, 0xa6, 0x6d, 0x61, 0x74, 0x72, 0x69, 0x78, 0xc7, 0x40  …  0x66, 0x5f, 0x64, 0x75, 0x6d, 0x6d, 0x79, 0

In [5]:
function create_net()
    net = Chain(
        Dense(22, 64, elu),
        Dense(64, 64, elu),
        Dense(64, 1)
    )
    loss = (x, lb, ub) -> begin
        y = net(x)
        sum(ifelse.(y .< lb, lb .- y, ifelse.(y .> ub, y .- ub, 0 .* y)))
    end
    net, loss
end

features(s::LearningMPC.Sample) = (s.state, s.mip.objective_bound, s.mip.objective_value)

features (generic function with 1 method)

In [15]:
xstar = BoxValkyries.nominal_state(robot)
mpc_params = LearningMPC.MPCParams(
    Δt=0.05,
    horizon=10,
    mip_solver=GurobiSolver(Gurobi.Env(), OutputFlag=0, 
        TimeLimit=5,
        FeasibilityTol=1e-3),
    lcp_solver=GurobiSolver(Gurobi.Env(), OutputFlag=0))

Q, R = BoxValkyries.default_costs(robot)
feet = findbody.(robot.mechanism, ["lf", "rf"])
lqrsol = LearningMPC.LQRSolution(xstar, Q, R, mpc_params.Δt, Point3D.(default_frame.(feet), 0., 0., 0.))
# lqrsol.S .= 1 ./ mpc_params.Δt .* Q

net, loss = create_net()
tangent_net = FluxExtensions.TangentPropagator(net)
net_params = params(net)
optimizer = Flux.Optimise.ADAM(net_params)

net_qp_controller = let x_net = MechanismState(robot.mechanism)
    function (state)
        set_configuration!(x_net, configuration(state))
        set_velocity!(x_net, velocity(state))
        value, jac = tangent_net(Vector(state))
        m = Model(solver=mpc_params.mip_solver)
        _, results = LCPSim.optimize(x_net, robot.environment, mpc_params.Δt, 1, m)
        @assert length(results) == 1
        x = results[1].state.state
        u = results[1].input
        q = vec(Flux.Tracker.data(jac))
        @objective m Min u' * lqrsol.R * u + x' * lqrsol.Q * x + q' * x
        solve(m)
        getvalue(results[1].input)
    end
end

mpc_controller = LearningMPC.MPCController(robot.mechanism, 
    robot.environment, mpc_params, lqrsol, 
    [lqrsol, net_qp_controller]);

sample_sink = LearningMPC.MPCSampleSink{Float64}(true)
playback_sink = LearningMPC.PlaybackSink(mvis, mpc_params.Δt)

mpc_controller.callback = LearningMPC.call_each(
    sample_sink,
    playback_sink,
)

live_viewer = LearningMPC.live_viewer(mvis)

termination = x -> begin
    (configuration(x)[2] < 0.5 || 
     configuration(x)[3] > π/4 ||
     configuration(x)[3] < -π/4)
end

dagger_controller = LearningMPC.call_each(
    LearningMPC.dagger_controller(
        mpc_controller,
        net_qp_controller,
        0.2),
    live_viewer
    )

dataset = LearningMPC.Dataset(lqrsol)

x_init = BoxValkyries.nominal_state(robot)
x0 = MechanismState{Float64}(robot.mechanism)

function collect_into!(data::Vector{<:LearningMPC.Sample})
    empty!(sample_sink)
    LearningMPC.randomize!(x0, x_init, 0.0, 1.5)
    results = LCPSim.simulate(x0, 
        dagger_controller,
        robot.environment, mpc_params.Δt, 50, 
        mpc_params.lcp_solver;
        termination=termination);
    append!(data, sample_sink.samples)
end


collect_into! (generic function with 1 method)

In [18]:
datasets = Vector{LearningMPC.Dataset{Float64}}()
all_training_data = Vector{Tuple{Vector{Float64}, Float64, Float64}}()
all_validation_data = Vector{Tuple{Vector{Float64}, Float64, Float64}}()
losses = Vector{Tuple{Float64, Float64}}()

@showprogress for i in 1:100
    dataset = LearningMPC.Dataset(lqrsol)
    for i in 1:2
        collect_into!(dataset.training_data)
    end
    collect_into!(dataset.testing_data)
    collect_into!(dataset.validation_data)
    append!(all_training_data, features.(dataset.training_data))
    append!(all_validation_data, features.(dataset.validation_data))
    filter!(all_training_data) do x
        !(any(isnan, x[1]) || isnan(x[2]) || isnan(x[3]))
    end
    filter!(all_validation_data) do x
        !(any(isnan, x[1]) || isnan(x[2]) || isnan(x[3]))
    end
    
    @time for i in 1:20
        Flux.train!(loss, shuffleobs(all_training_data), optimizer)
        push!(losses, 
            (mean(xy -> Flux.Tracker.data(loss(xy...)), 
                  all_training_data),
             mean(xy -> Flux.Tracker.data(loss(xy...)), 
                  all_validation_data)))
    end
    push!(datasets, dataset)
    
    jldopen("box-atlas-value-interval.jld2", "w") do file
        file["datasets"] = datasets
        file["net"] = net
        file["lqrsol"] = lqrsol
        file["mpc_params"] = Dict(
            "Δt" => mpc_params.Δt,
            "horizon" => mpc_params.horizon,
        )
        file["all_training_data"] = all_training_data
        file["all_validation_data"] = all_validation_data
        file["losses"] = losses
    end
    
    plt = plot(first.(losses), label="training")
    plot!(plt, last.(losses), label="validation")
    ylims!(plt, (0, ylims(plt)[2]))
    display(plt)
end

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 5 
 
 
 10 
 
 
 15 
 
 
 20 
 
 
 0 
 
 
 20 
 
 
 40 
 
 
 60 
 
 
 80 
 
 
 100 
 
 
 120 
 
 
 
 
 
 
 
 training 
 
 
 
 validation

  0.239717 seconds (185.67 k allocations: 15.783 MiB)


Progress:   1%|                                         |  ETA: 6:09:15

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 10 
 
 
 20 
 
 
 30 
 
 
 40 
 
 
 0 
 
 
 20 
 
 
 40 
 
 
 60 
 
 
 80 
 
 
 100 
 
 
 120 
 
<polyline clip-path="url(#clip5502)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 35.8198,42.257 49.7812,47.3613 63.7426,53.7385 77.704,61.1027 91.6654,69.8922 105.627,78.8218 119.588,87.7266 133.55,93.6735 147.511,97.0999 161.473,101.034 
 175.434,104.435 189.395,108.295 203.357,110.35 217.318,112.077 231.28,114.234 245.241,117.291 259.202,120.132 273.164,123.122 287.125,126.844 301.087,130.946 
 315.048,155.516 329.009,160.594 342.971,164.194 356.932,169.558 370.894,172.463 384.855,175.301 398.817,177.507 412.778,180.478 426.739,182.565 440.701,185.895 
 454.662,189.386 468.624,191.578 482.585,196.72 496.546,199.598 510.508,203.136 524.469,206.126 538.431,208.859 552.392,211.954 566.354,214.619 580.315,217.277 
 
 "/>
<polyline clip-path="url(#clip5502)" style="stroke:#e26f46; stroke-width:1; stroke-opacity:1; fill:none" points="
 35.8198,11.811 49.7812,14.8038 63.7426,18.2458 77.704,22.6172 91.6654,28.3362 105.627,34.6793 119.588,41.9865 133.55,50.7575 147.511,53.8789 161.473,57.5421 
 175.434,59.8884 189.395,63.6113 203.357,65.145 217.318,66.1721 231.28,68.1843 245.241,69.8581 259.202,69.2622 273.164,69.2621 287.125,71.5584 301.087,71.2503 
 315.048,199.866 329.009,208.48 342.971,212.817 356.932,222.341 370.894,223.666 384.855,229.896 398.817,229.029 412.778,233.944 426.739,231.651 440.701,236.502 
 454.662,244.005 468.624,246.425 482.585,251.149 496.546,249.958 510.508,247.589 524.469,243.277 538.431,240.948 552.392,238.948 566.354,235.437 580.315,229.835 
 
 "/>
 
 
 
 
 training 
 
 
 
 validation

  0.422717 seconds (389.96 k allocations: 34.457 MiB, 4.28% gc time)


...

 18.813435 seconds (19.62 M allocations: 1.689 GiB, 3.27% gc time)


Progress:  99%|█████████████████████████████████████████|  ETA: 0:04:32

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 500 
 
 
 1000 
 
 
 1500 
 
 
 2000 
 
 
 0 
 
 
 25 
 
 
 50 
 
 
 75 
 
 
 100 
 
 
 125 
 
<polyline clip-path="url(#clip5102)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 35.8198,51.7913 36.0922,56.7498 36.3646,62.9447 36.6369,70.0984 36.9093,78.6367 37.1817,87.3111 37.4541,95.9614 37.7265,101.738 37.9989,105.067 38.2712,108.889 
 38.5436,112.192 38.816,115.942 39.0884,117.938 39.3608,119.616 39.6332,121.712 39.9055,124.681 40.1779,127.44 40.4503,130.345 40.7227,133.961 40.9951,137.946 
 41.2675,161.814 41.5398,166.746 41.8122,170.244 42.0846,175.454 42.357,178.276 42.6294,181.033 42.9018,183.176 43.1741,186.062 43.4465,188.09 43.7189,191.324 
 43.9913,194.715 44.2637,196.845 44.5361,201.84 44.8085,204.636 45.0808,208.072 45.3532,210.977 45.6256,213.632 45.898,216.639 46.1704,219.227 46.4428,221.81 
 46.7151,209.047 46.9875,234.473 47.2599,243.347 47.5323,251.071 47.8047,256.441 48.0771,263.134 48.3494,267.638 48.6218,271.167 48.8942,274.079 49.1666,276.936 
 49.439,279.68 49.7114,282.099 49.9837,282.137 50.2561,284.195 50.5285,284.252 50.8009,287.015 51.0733,288.85 51.3457,290.134 51.618,291.742 51.8904,292.702 
 52.1628,77.3686 52.4352,83.1485 52.7076,89.0119 52.98,94.2707 53.2523,97.1387 53.5247,102.585 53.7971,105.602 54.0695,111.532 54.3419,115.309 54.6143,120.117 
 54.8867,123.327 55.159,127.443 55.4314,130.875 55.7038,132.167 55.9762,136.481 56.2486,140.304 56.521,143.516 56.7933,142.236 57.0657,149.541 57.3381,151.639 
 57.6105,177.364 57.8829,182.946 58.1553,188.367 58.4276,191.307 58.7,195.777 58.9724,202.591 59.2448,206.957 59.5172,209.929 59.7896,215.303 60.0619,219.107 
 60.3343,220.354 60.6067,227.104 60.8791,231.139 61.1515,235.61 61.4239,238.697 61.6962,240.483 61.9686,240.558 62.241,245.176 62.5134,248.025 62.7858,252.962 
 63.0582,254.141 63.3305,259.818 63.6029,266.731 63.8753,261.652 64.1477,274.995 64.4201,277.795 64.6925,282.587 64.9649,281.151 65.2372,289.476 65.5096,295.224 
 65.782,298.9 66.0544,296.515 66.3268,297.354 66.5992,310.888 66.8715,306.191 67.1439,314.432 67.4163,320.859 67.6887,322.636 67.9611,323.916 68.2335,324.284 
 68.5058,325.688 68.7782,329.43 69.0506,326.093 69.323,333.297 69.5954,335.847 69.8678,333.296 70.1401,328.412 70.4125,338.114 70.6849,333.126 70.9573,329.2 
 71.2297,340.577 71.5021,342.968 71.7744,344.476 72.0468,348.3 72.3192,346.847 72.5916,348.464 72.864,350.246 73.1364,346.191 73.4087,354.308 73.6811,353.69 
 73.9535,330.337 74.2259,331.944 74.4983,334.933 74.7707,338.673 75.0431,341.813 75.3154,343.077 75.5878,342.693 75.8602,348.154 76.1326,344.169 76.405,346.997 
 76.6774,349.481 76.9497,352.032 77.2221,349.845 77.4945,351.096 77.7669,353.038 78.0393,351.362 78.3117,354.198 78.584,353.869 78.8564,356.991 79.1288,355.515 
 79.4012,345.206 79.6736,351.581 79.946,354.811 80.2183,355.858 80.4907,348.27 80.7631,355.707 81.0355,360.883 81.3079,360.237 81.5803,355.393 81.8526,363.966 
 82.125,363.382 82.3974,360.348 82.6698,362.143 82.9422,363.693 83.2146,364.286 83.4869,366.932 83.7593,367.141 84.0317,366.74 84.3041,365.829 84.5765,366.463 
 84.8489,360.464 85.1213,361.618 85.3936,342.937 85.666,363.18 85.9384,364.84 86.2108,358.741 86.4832,359.888 86.7556,362.752 87.0279,357.092 87.3003,367.733 
 87.5727,360.087 87.8451,366.479 88.1175,366.272 88.3899,364.312 88.6622,368.037 88.9346,365.837 89.207,369.827 89.4794,367.594 89.7518,369.128 90.0242,368.61 
 90.2965,352.505 90.5689,360.668 90.8413,357.313 91.1137,364.227 91.3861,363.918 91.6585,364.131 91.9308,359.411 92.2032,365.68 92.4756,363.501 92.748,363.452 
 93.0204,363.005 93.2928,367.924 93.5651,366.848 93.8375,367.594 94.1099,368.753 94.3823,364.445 94.6547,368.184 94.9271,368.301 95.1995,362.628 95.4718,370.798 
 95.7442,320.988 96.0166,330.756 96.289,327.773 96.5614,324.525 96.8338,339.901 97.1061,342.015 97.3785,337.976 97.6509,343.925 97.9233,344.46 98.195

 19.092336 seconds (19.83 M allocations: 1.708 GiB, 3.19% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 7:33:09


In [19]:
println("finished")

finished
